<a href="https://www.kaggle.com/code/klimyuriy/beer-recomendation?scriptVersionId=197040634" target="_blank"><img align="left" alt="Kaggle" title="Open in Kaggle" src="https://kaggle.com/static/images/open-in-kaggle.svg"></a>

In [1]:
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

import matplotlib.pyplot as plt
import seaborn as sns

import plotly.express as px
import plotly.graph_objects as go
from surprise import BaselineOnly
from surprise import KNNBasic
from surprise import BaselineOnly, accuracy
from surprise import CoClustering
import pandas as pd
from surprise.model_selection import train_test_split

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

/kaggle/input/beerreviews/beer_reviews.csv


In [2]:
!pip install -q surprise

In [3]:
df = pd.read_csv('/kaggle/input/beerreviews/beer_reviews.csv')
df

brewery_id                 brewery_name  review_time  review_overall  \
0             10325              Vecchio Birraio   1234817823             1.5   
1             10325              Vecchio Birraio   1235915097             3.0   
2             10325              Vecchio Birraio   1235916604             3.0   
3             10325              Vecchio Birraio   1234725145             3.0   
4              1075      Caldera Brewing Company   1293735206             4.0   
...             ...                          ...          ...             ...   
1586609       14359  The Defiant Brewing Company   1162684892             5.0   
1586610       14359  The Defiant Brewing Company   1161048566             4.0   
1586611       14359  The Defiant Brewing Company   1160702513             4.5   
1586612       14359  The Defiant Brewing Company   1160023044             4.0   
1586613       14359  The Defiant Brewing Company   1160005319             5.0   

         review_aroma  review_appearance review_profilename  \
0                 2.0                2.5            stcules   
1                 2.5                3.0            stcules   
2                 2.5                3.0            stcules   
3                 3.0                3.5            stcules   
4                 4.5                4.0     johnmichaelsen   
...               ...                ...                ...   
1586609           4.0                3.5         maddogruss   
1586610           5.0                2.5          yelterdow   
1586611           3.5                3.0           TongoRad   
1586612           4.5                4.5           dherling   
1586613           4.5                4.5               cbl2   

                             beer_style  review_palate  review_taste  \
0                            Hefeweizen            1.5           1.5   
1                    English Strong Ale            3.0           3.0   
2                Foreign / Export Stout            3.0           3.0   
3                       German Pilsener            2.5           3.0   
4        American Double / Imperial IPA            4.0           4.5   
...                                 ...            ...           ...   
1586609                     Pumpkin Ale            4.0           4.0   
1586610                     Pumpkin Ale            2.0           4.0   
1586611                     Pumpkin Ale            3.5           4.0   
1586612                     Pumpkin Ale            4.5           4.5   
1586613                     Pumpkin Ale            4.5           4.5   

                      beer_name  beer_abv  beer_beerid  
0                  Sausa Weizen       5.0        47986  
1                      Red Moon       6.2        48213  
2        Black Horse Black Beer       6.5        48215  
3                    Sausa Pils       5.0        47969  
4                 Cauldron DIPA       7.7        64883  
...                         ...       ...          ...  
1586609      The Horseman's Ale       5.2        33061  
1586610      The Horseman's Ale       5.2        33061  
1586611      The Horseman's Ale       5.2        33061  
1586612      The Horseman's Ale       5.2        33061  
1586613      The Horseman's Ale       5.2        33061  

[1586614 rows x 13 columns]

In [4]:
df.describe()

brewery_id   review_time  review_overall  review_aroma  \
count  1.586614e+06  1.586614e+06    1.586614e+06  1.586614e+06   
mean   3.130099e+03  1.224089e+09    3.815581e+00  3.735636e+00   
std    5.578104e+03  7.654427e+07    7.206219e-01  6.976167e-01   
min    1.000000e+00  8.406720e+08    0.000000e+00  1.000000e+00   
25%    1.430000e+02  1.173224e+09    3.500000e+00  3.500000e+00   
50%    4.290000e+02  1.239203e+09    4.000000e+00  4.000000e+00   
75%    2.372000e+03  1.288568e+09    4.500000e+00  4.000000e+00   
max    2.800300e+04  1.326285e+09    5.000000e+00  5.000000e+00   

       review_appearance  review_palate  review_taste      beer_abv  \
count       1.586614e+06   1.586614e+06  1.586614e+06  1.518829e+06   
mean        3.841642e+00   3.743701e+00  3.792860e+00  7.042387e+00   
std         6.160928e-01   6.822184e-01  7.319696e-01  2.322526e+00   
min         0.000000e+00   1.000000e+00  1.000000e+00  1.000000e-02   
25%         3.500000e+00   3.500000e+00  3.500000e+00  5.200000e+00   
50%         4.000000e+00   4.000000e+00  4.000000e+00  6.500000e+00   
75%         4.000000e+00   4.000000e+00  4.500000e+00  8.500000e+00   
max         5.000000e+00   5.000000e+00  5.000000e+00  5.770000e+01   

        beer_beerid  
count  1.586614e+06  
mean   2.171279e+04  
std    2.181834e+04  
min    3.000000e+00  
25%    1.717000e+03  
50%    1.390600e+04  
75%    3.944100e+04  
max    7.731700e+04

In [5]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1586614 entries, 0 to 1586613
Data columns (total 13 columns):
 #   Column              Non-Null Count    Dtype  
---  ------              --------------    -----  
 0   brewery_id          1586614 non-null  int64  
 1   brewery_name        1586599 non-null  object 
 2   review_time         1586614 non-null  int64  
 3   review_overall      1586614 non-null  float64
 4   review_aroma        1586614 non-null  float64
 5   review_appearance   1586614 non-null  float64
 6   review_profilename  1586266 non-null  object 
 7   beer_style          1586614 non-null  object 
 8   review_palate       1586614 non-null  float64
 9   review_taste        1586614 non-null  float64
 10  beer_name           1586614 non-null  object 
 11  beer_abv            1518829 non-null  float64
 12  beer_beerid         1586614 non-null  int64  
dtypes: float64(6), int64(3), object(4)
memory usage: 157.4+ MB


In [6]:
print(df.isnull().sum())

brewery_id                0
brewery_name             15
review_time               0
review_overall            0
review_aroma              0
review_appearance         0
review_profilename      348
beer_style                0
review_palate             0
review_taste              0
beer_name                 0
beer_abv              67785
beer_beerid               0
dtype: int64


In [7]:
df = df.dropna(subset=['brewery_name', 'review_profilename'])

In [8]:
fig = px.histogram(df, x='review_overall', nbins=25, title='Distribution of overall ratings')
fig.update_xaxes(title_text='Overall rating')
fig.update_yaxes(title_text='Quantity')
fig.show()

In [9]:
beer_style_ratings = df.groupby('beer_style')['review_overall'].mean().sort_values(ascending=False).reset_index()
fig = px.bar(beer_style_ratings, y='beer_style', x='review_overall', orientation='h', title='Average Overall Beer Style Rating')
fig.update_xaxes(title_text='Average overall rating')
fig.update_yaxes(title_text='Beer style')
fig.show()

In [10]:
review_counts = df['beer_style'].value_counts().reset_index()
review_counts.columns = ['beer_style', 'count']

fig = px.bar(review_counts, x='beer_style', y='count', title='Number of ratings by beer style',
             labels={'count':'Number of ratings', 'beer_style':'Beer style'})
fig.show()

In [11]:
from sklearn.preprocessing import LabelEncoder

label_encoder = LabelEncoder()

df['review_profilename'] = label_encoder.fit_transform(df['review_profilename'])

/tmp/ipykernel_18/1305432232.py:5: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [12]:
df_test = df.sample(n=200000, random_state=42)

In [13]:
from surprise import Dataset, SVD, Reader, SVDpp, NMF

reader = Reader(rating_scale=(0, 5))

data = Dataset.load_from_df(df_test[["review_profilename", "beer_beerid", "review_overall"]], reader)

In [14]:
trainset, testset = train_test_split(data, train_size=0.8)

In [15]:
!pip install optuna
import optuna

In [16]:
def objective(trial):
    try:
        algorithm = trial.suggest_categorical('algorithm', ['BaselineOnly', 'SVD', 'SVDpp', 'NMF', 'KNNBasic', 'CoClustering'])
        print(f"Starting trial with algorithm: {algorithm}")

        if algorithm == 'BaselineOnly':
            method = trial.suggest_categorical('method', ['als', 'sgd'])
            reg_u = trial.suggest_float('reg_u', 1e-5, 1e-1, log=True)
            reg_i = trial.suggest_float('reg_i', 1e-5, 1e-1, log=True)
            bsl_options = {'method': method, 'reg_u': reg_u, 'reg_i': reg_i}
            algo = BaselineOnly(bsl_options=bsl_options)

        elif algorithm == 'SVD':
            n_factors = trial.suggest_int('n_factors', 5, 50)
            n_epochs = trial.suggest_int('n_epochs', 5, 50)
            lr_all = trial.suggest_float('lr_all', 1e-4, 1e-1, log=True)
            reg_all = trial.suggest_float('reg_all', 1e-4, 1e-1, log=True)
            algo = SVD(n_factors=n_factors, n_epochs=n_epochs, lr_all=lr_all, reg_all=reg_all)

        elif algorithm == 'SVDpp':
            n_factors = trial.suggest_int('n_factors', 5, 50)
            n_epochs = trial.suggest_int('n_epochs', 5, 50)
            lr_all = trial.suggest_float('lr_all', 1e-4, 1e-1, log=True)
            reg_all = trial.suggest_float('reg_all', 1e-4, 1e-1, log=True)
            algo = SVDpp(n_factors=n_factors, n_epochs=n_epochs, lr_all=lr_all, reg_all=reg_all)

        elif algorithm == 'NMF':
            n_factors = trial.suggest_int('n_factors', 10, 50)
            n_epochs = trial.suggest_int('n_epochs', 5, 30)
            reg_pu = trial.suggest_float('reg_pu', 1e-4, 1e-1, log=True)
            reg_qi = trial.suggest_float('reg_qi', 1e-4, 1e-1, log=True)
            algo = NMF(n_factors=n_factors, n_epochs=n_epochs, reg_pu=reg_pu, reg_qi=reg_qi)

        elif algorithm == 'KNNBasic':
            k = trial.suggest_int('k', 10, 50)
            min_k = trial.suggest_int('min_k', 1, 15)
            sim_options = {
                'name': trial.suggest_categorical('name', ['cosine', 'pearson']),
                'user_based': trial.suggest_categorical('user_based', [True, False])
            }
            algo = KNNBasic(k=k, min_k=min_k, sim_options=sim_options, n_jobs=-1)

        elif algorithm == 'CoClustering':
            n_cltr_u = trial.suggest_int('n_cltr_u', 3, 10)
            n_cltr_i = trial.suggest_int('n_cltr_i', 3, 10)
            n_epochs = trial.suggest_int('n_epochs', 20, 100)
            algo = CoClustering(n_cltr_u=n_cltr_u, n_cltr_i=n_cltr_i, n_epochs=n_epochs)

        print("Fitting the model...")
        algo.fit(trainset)
        
        print("Testing the model...")
        predictions = algo.test(testset)
        
        rmse = accuracy.rmse(predictions, verbose=False)
        print(f"RMSE: {rmse}")
        
        return rmse

    except Exception as e:
        print(f"Trial failed with exception: {e}")
        raise optuna.exceptions.TrialPruned()


In [17]:
study = optuna.create_study(direction="minimize")
study.optimize(objective, n_trials=500)

[I 2024-09-17 16:01:54,019] A new study created in memory with name: no-name-98bf62f1-28df-4f3e-9ca6-12f1aa667294


Starting trial with algorithm: SVDpp
Fitting the model...
Testing the model...


[I 2024-09-17 16:03:58,619] Trial 0 finished with value: 0.7250432521533726 and parameters: {'algorithm': 'SVDpp', 'n_factors': 37, 'n_epochs': 28, 'lr_all': 0.029321617278394305, 'reg_all': 0.003557932313784824}. Best is trial 0 with value: 0.7250432521533726.


RMSE: 0.7250432521533726
Starting trial with algorithm: NMF
Fitting the model...
Testing the model...


[I 2024-09-17 16:04:00,655] Trial 1 finished with value: 0.74061987500048 and parameters: {'algorithm': 'NMF', 'n_factors': 14, 'n_epochs': 5, 'reg_pu': 0.014880705469525829, 'reg_qi': 0.040060904313489645}. Best is trial 0 with value: 0.7250432521533726.


...

RMSE: 0.639199873976952
Starting trial with algorithm: BaselineOnly
Fitting the model...
Estimating biases using sgd...
Testing the model...


[I 2024-09-17 17:22:51,332] Trial 498 finished with value: 0.639199873976952 and parameters: {'algorithm': 'BaselineOnly', 'method': 'sgd', 'reg_u': 0.029794320196115776, 'reg_i': 2.651557146606066e-05}. Best is trial 18 with value: 0.639199873976952.


RMSE: 0.639199873976952
Starting trial with algorithm: BaselineOnly
Fitting the model...
Estimating biases using sgd...
Testing the model...


[I 2024-09-17 17:22:53,839] Trial 499 finished with value: 0.639199873976952 and parameters: {'algorithm': 'BaselineOnly', 'method': 'sgd', 'reg_u': 0.07008652328391987, 'reg_i': 0.00018721139382126215}. Best is trial 18 with value: 0.639199873976952.


RMSE: 0.639199873976952


In [18]:
study.best_params

{'algorithm': 'BaselineOnly',
 'method': 'sgd',
 'reg_u': 0.05288486083593057,
 'reg_i': 1.1782837859040896e-05}

In [19]:
params = {'algorithm': 'SVD',
          'n_factors': 12,
          'n_epochs': 37,
          'lr_all': 0.005081717895895894,
          'reg_all': 0.07572454352409166}

In [20]:
data_overall = Dataset.load_from_df(df[["review_profilename", "beer_beerid", "review_overall"]], reader)

trainset_overall, testset_overall = train_test_split(data, train_size=0.8)

In [21]:
from surprise import BaselineOnly, SVD, KNNBasic, CoClustering, accuracy

class RecommenderSystem:
    def __init__(self, params, trainset, testset):
        self.params = params
        self.trainset = trainset
        self.testset = testset
        self.algo = self._select_algorithm()

    def _select_algorithm(self):
        best_algorithm = self.params['algorithm']

        if best_algorithm == 'BaselineOnly':
            bsl_options = {
                'method': self.params['method'],
                'reg_u': self.params['reg_u'],
                'reg_i': self.params['reg_i']
            }
            return BaselineOnly(bsl_options=bsl_options)

        elif best_algorithm == 'SVD':
            return SVD(
                n_factors=self.params['n_factors'],
                n_epochs=self.params['n_epochs'],
                lr_all=self.params['lr_all'],
                reg_all=self.params['reg_all']
            )

        elif best_algorithm == 'KNNBasic':
            sim_options = {
                'name': self.params['name'],
                'user_based': self.params['user_based']
            }
            return KNNBasic(
                k=self.params['k'],
                min_k=self.params['min_k'],
                sim_options=sim_options
            )

        elif best_algorithm == 'CoClustering':
            return CoClustering(
                n_cltr_u=self.params['n_cltr_u'],
                n_cltr_i=self.params['n_cltr_i'],
                n_epochs=self.params['n_epochs']
            )
    
    def train(self):
        print("Training the model...")
        self.algo.fit(self.trainset)

    def evaluate(self):
        print("Evaluating the model...")
        final_predictions = self.algo.test(self.testset)
        
        mae = accuracy.mae(final_predictions, verbose=False)
        mse = accuracy.mse(final_predictions, verbose=False)
        rmse = accuracy.rmse(final_predictions, verbose=False)
        fcp = accuracy.fcp(final_predictions, verbose=False)

        return {
            'MAE': mae,
            'MSE': mse,
            'RMSE': rmse,
            'FCP': fcp
        }

    def predict(self, uid, iid):
        return self.algo.predict(uid, iid)

In [22]:
recommender_overall = RecommenderSystem(params, trainset_overall, testset_overall)

recommender_overall.train()

results = recommender_overall.evaluate()
print(f"MAE: {results['MAE']}")
print(f"MSE: {results['MSE']}")
print(f"RMSE: {results['RMSE']}")
print(f"FCP: {results['FCP']}")

prediction_overall = recommender_overall.predict(uid=23775, iid=28113)
print(prediction_overall)

Training the model...
Evaluating the model...
MAE: 0.47157430031971387
MSE: 0.3949455802966383
RMSE: 0.6284469590161434
FCP: 0.6215983910055204
user: 23775      item: 28113      r_ui = None   est = 3.82   {'was_impossible': False}


In [23]:
best_params = study.best_params

best_algorithm = best_params['algorithm']

if best_algorithm == 'BaselineOnly':
    bsl_options = {
        'method': best_params['method'],
        'reg_u': best_params['reg_u'],
        'reg_i': best_params['reg_i']
    }
    overall_algo = BaselineOnly(bsl_options=bsl_options)

elif best_algorithm == 'SVD':
    overall_algo = SVD(
        n_factors=best_params['n_factors'],
        n_epochs=best_params['n_epochs'],
        lr_all=best_params['lr_all'],
        reg_all=best_params['reg_all']
    )

elif best_algorithm == 'KNNBasic':
    sim_options = {
        'name': best_params['name'],
        'user_based': best_params['user_based']
    }
    overall_algo = KNNBasic(
        k=best_params['k'],
        min_k=best_params['min_k'],
        sim_options=sim_options
    )

elif best_algorithm == 'CoClustering':
    overall_algo = CoClustering(
        n_cltr_u=best_params['n_cltr_u'],
        n_cltr_i=best_params['n_cltr_i'],
        n_epochs=best_params['n_epochs']
    )

overall_algo.fit(trainset)

final_predictions = overall_algo.test(testset)

print(f"mae = {accuracy.mae(final_predictions, verbose=False)}")
print(f"mse = {accuracy.mse(final_predictions, verbose=False)}")
print(f"rmse= {accuracy.rmse(final_predictions, verbose=False)}")
print(f"fcp = {accuracy.fcp(final_predictions, verbose=False)}")

Estimating biases using sgd...
mae = 0.4787717456076991
mse = 0.4085764788921513
rmse= 0.639199873976952
fcp = 0.6186449675553297


In [24]:
df['review_profilename']

0          30566
1          30566
2          30566
3          30566
4          23008
           ...  
1586609    24775
1586610    33151
1586611    12503
1586612    18486
1586613    16714
Name: review_profilename, Length: 1586251, dtype: int64

In [25]:
df['beer_beerid']

0          47986
1          48213
2          48215
3          47969
4          64883
           ...  
1586609    33061
1586610    33061
1586611    33061
1586612    33061
1586613    33061
Name: beer_beerid, Length: 1586251, dtype: int64

In [26]:
data_aroma = Dataset.load_from_df(df[["review_profilename", "beer_beerid", "review_aroma"]], reader)

trainset_aroma, testset_aroma = train_test_split(data_aroma, train_size=0.8)

In [27]:
recommender_aroma = RecommenderSystem(params, trainset_aroma, testset_aroma)

recommender_aroma.train()

results = recommender_aroma.evaluate()
print(f"MAE: {results['MAE']}")
print(f"MSE: {results['MSE']}")
print(f"RMSE: {results['RMSE']}")
print(f"FCP: {results['FCP']}")

prediction_aroma = recommender_aroma.predict(uid=23775, iid=28113)
print(prediction_aroma)

Training the model...
Evaluating the model...
MAE: 0.39681706667359007
MSE: 0.2745192858826494
RMSE: 0.523945880681058
FCP: 0.7288247880072136
user: 23775      item: 28113      r_ui = None   est = 3.65   {'was_impossible': False}


In [28]:
data_appearance = Dataset.load_from_df(df[["review_profilename", "beer_beerid", "review_appearance"]], reader)

trainset_appearance, testset_appearance = train_test_split(data_appearance, train_size=0.8)

In [29]:
recommender_appearance = RecommenderSystem(params, trainset_appearance, testset_appearance)

recommender_appearance.train()

results = recommender_appearance.evaluate()
print(f"MAE: {results['MAE']}")
print(f"MSE: {results['MSE']}")
print(f"RMSE: {results['RMSE']}")
print(f"FCP: {results['FCP']}")

prediction_appearance = recommender_appearance.predict(uid=23775, iid=28113)
print(prediction_appearance)

Training the model...
Evaluating the model...
MAE: 0.364582319553614
MSE: 0.23206181712935864
RMSE: 0.4817279492922936
FCP: 0.6992526969088022
user: 23775      item: 28113      r_ui = None   est = 3.64   {'was_impossible': False}


In [30]:
data_palate = Dataset.load_from_df(df[["review_profilename", "beer_beerid", "review_palate"]], reader)

trainset_palate, testset_palate = train_test_split(data_palate, train_size=0.8)

In [31]:
recommender_palate = RecommenderSystem(params, trainset_palate, testset_palate)

recommender_palate.train()

results = recommender_palate.evaluate()
print(f"MAE: {results['MAE']}")
print(f"MSE: {results['MSE']}")
print(f"RMSE: {results['RMSE']}")
print(f"FCP: {results['FCP']}")

prediction_palate = recommender_palate.predict(uid=23775, iid=28113)
print(prediction_palate)

Training the model...
Evaluating the model...
MAE: 0.4102738047542338
MSE: 0.2947696178274945
RMSE: 0.5429268991563179
FCP: 0.6974144056289887
user: 23775      item: 28113      r_ui = None   est = 3.55   {'was_impossible': False}


In [32]:
data_taste = Dataset.load_from_df(df[["review_profilename", "beer_beerid", "review_taste"]], reader)

trainset_taste, testset_taste = train_test_split(data_taste, train_size=0.8)

In [33]:
recommender_taste = RecommenderSystem(params, trainset_taste, testset_taste)

recommender_taste.train()

results = recommender_taste.evaluate()
print(f"MAE: {results['MAE']}")
print(f"MSE: {results['MSE']}")
print(f"RMSE: {results['RMSE']}")
print(f"FCP: {results['FCP']}")

prediction_taste = recommender_taste.predict(uid=23775, iid=28113)
print(prediction_taste)

Training the model...
Evaluating the model...
MAE: 0.4206063321221472
MSE: 0.3178311819829919
RMSE: 0.5637651833724675
FCP: 0.7265108733436668
user: 23775      item: 28113      r_ui = None   est = 3.64   {'was_impossible': False}


In [34]:
class BeerRecommender:
    def __init__(self, df, recommender_overall, recommender_aroma, recommender_appearance, recommender_palate, recommender_taste):
        self.df = df
        self.recommender_overall = recommender_overall
        self.recommender_aroma = recommender_aroma
        self.recommender_appearance = recommender_appearance
        self.recommender_palate = recommender_palate
        self.recommender_taste = recommender_taste

    def recommend_beer(self, user_id, beer_name, user_ratings):
        if beer_name not in self.df['beer_name'].values:
            print("This beer does not exist")
            return

        beer_id = self.df[self.df['beer_name'] == beer_name]['beer_beerid'].values[0]

        print(f"Predicting best beers for user {user_id}...")

        other_beers = self.df[self.df['beer_beerid'] != beer_id]['beer_beerid'].unique()

        predictions_aroma = []
        predictions_appearance = []
        predictions_palate = []
        predictions_taste = []
        predictions_overall = []

        for beer in other_beers:
            predictions_aroma.append((beer, self.recommender_aroma.predict(user_id, beer).est))
            predictions_appearance.append((beer, self.recommender_appearance.predict(user_id, beer).est))
            predictions_palate.append((beer, self.recommender_palate.predict(user_id, beer).est))
            predictions_taste.append((beer, self.recommender_taste.predict(user_id, beer).est))
            predictions_overall.append((beer, self.recommender_overall.predict(user_id, beer).est))

        best_aroma = sorted(predictions_aroma, key=lambda x: x[1], reverse=True)[0]
        best_appearance = sorted(predictions_appearance, key=lambda x: x[1], reverse=True)[0]
        best_palate = sorted(predictions_palate, key=lambda x: x[1], reverse=True)[0]
        best_taste = sorted(predictions_taste, key=lambda x: x[1], reverse=True)[0]
        best_overall = sorted(predictions_overall, key=lambda x: x[1], reverse=True)[0]

        combined_predictions = []
        for beer in other_beers:
            combined_score = (
                self.recommender_aroma.predict(user_id, beer).est * 0.2 +
                self.recommender_appearance.predict(user_id, beer).est * 0.2 +
                self.recommender_palate.predict(user_id, beer).est * 0.2 +
                self.recommender_taste.predict(user_id, beer).est * 0.2 +
                self.recommender_overall.predict(user_id, beer).est * 0.2
            )
            combined_predictions.append((beer, combined_score))

        best_combined = sorted(combined_predictions, key=lambda x: x[1], reverse=True)[:3]

        print(f"Best beer for aroma: {self._get_beer_name(best_aroma[0])} - with predicted score {best_aroma[1]:.2f}")
        print(f"Best beer for appearance: {self._get_beer_name(best_appearance[0])} - with predicted score {best_appearance[1]:.2f}")
        print(f"Best beer for palate: {self._get_beer_name(best_palate[0])} - with predicted score {best_palate[1]:.2f}")
        print(f"Best beer for taste: {self._get_beer_name(best_taste[0])} - with predicted score {best_taste[1]:.2f}")
        print("Best beers overall:")
        for beer, score in best_combined:
            print(f"{self._get_beer_name(beer)} - with combined score {score:.2f}")

    def _get_beer_name(self, beer_id):
        return self.df[self.df['beer_beerid'] == beer_id]['beer_name'].values[0]

In [35]:
user_ratings = {
    'review_aroma': 3,
    'review_appearance': 4.5,
    'review_palate': 4,
    'review_taste': 4,
    'review_overall': 4
}

beer_recommender = BeerRecommender(df, recommender_overall, recommender_aroma, recommender_appearance, recommender_palate, recommender_taste)

beer_recommender.recommend_beer(user_id=123456, beer_name="The Horseman's Ale", user_ratings=user_ratings)

Predicting best beers for user 123456...
Best beer for aroma: Armand'4 Oude Geuze Lente (Spring) - with predicted score 4.77
Best beer for appearance: St-Ambroise Stout Impériale Russe - with predicted score 4.66
Best beer for palate: Rare D.O.S. - with predicted score 4.73
Best beer for taste: M Belgian-Style Barleywine - with predicted score 4.87
Best beers overall:
Armand'4 Oude Geuze Lente (Spring) - with combined score 4.64
Pliny The Younger - with combined score 4.60
Trappist Westvleteren 12 - with combined score 4.60
